# processMeerKAT Jupyter Notebook Tutorial

processMeerKAT implements a CASA based wide-band full Stokes calibration pipeline (in the linear basis). Broadly, the pipeline aims to “do the right thing” and by keeping the steps as general as possible we believe that there should be no need for fine tuning in order to obtain a well calibrated dataset.

This Jupyter Notebook Tutorial is based on the [processMeerKAT](https://idia-pipelines.github.io/docs/processMeerKAT) documentation for the IDIA processMeerKAT Pipeline.

In [1]:
casa['build']['version']

'5.5.0-149  '

In [2]:
from __future__ import print_function
import sys
import os
import subprocess

home = !pwd

## singularity data path:
#data_path = os.path.join(home[0],'data/')

## singularity pipeline path:
pipeline_path = os.path.join(home[0],'pipelines/processMeerKAT/')
functions_path = os.path.join(home[0],'pipelines/processMeerKAT/cal_scripts/')

## singularity module paths:
sys.path.append(pipeline_path)
sys.path.append(functions_path)


In [3]:
### View config file

f = open('myconfig.txt', 'r')
file_contents = f.read()
print(file_contents)
f.close()

[crosscal]
minbaselines = 4                  # Minimum number of baselines to use while calibrating
specavg = 1                       # Number of channels to average after calibration (during split)
timeavg = '8s'                    # Time interval to average after calibration (during split)
keepmms = True                    # Output MMS (True) or MS (False) during split
spw = '0:860~1700MHz'             # Spectral window / frequencies to extract for MMS
calcrefant = True                 # Calculate reference antenna in program (overwrites 'refant')
refant = 'm005'                   # Reference antenna name / number
standard = 'Perley-Butler 2010'   # Flux density standard for setjy
badants = []                      # List of bad antenna numbers (to flag)
badfreqranges = [ '935~947MHz',   # List of bad frequency ranges (to flag)
	'1160~1310MHz',
	'1476~1611MHz',
	'1670~1700MHz']

[slurm]
nodes = 6
ntasks_per_node = 4
plane = 2
mem = 236
partition = 'Main'
time = '12:00:00'
submit = Fal

## Input validation 

This script performs a few basic validity checks, on the default config file, and on the input MS. the existence of the input MS, and the data types of the inputs specified in the config file are all verified before the pipeline continues to the next steps. If reference antenna calculation is not requested, a simple check is performed to verify that the input reference antenna exists in the MS. Otherwise, the following paragraph describes the details of reference antenna calculation.

In [4]:
run pipelines/processMeerKAT/cal_scripts/validate_input.py --config myconfig.txt

2019-08-07 10:54:14,012 INFO: This is version 1.0 of the pipeline


# Reference antenna calculation 

If the `calcrefant` parameter in the config file is set to `True`, then this script is executed. The algorithm works by calculating the median and standard deviation over all the visibility amplitudes for a given antenna, and iterates over every antenna in the array. Any outlier antennas, in the top 2 and bottom 5 percentile of this distribution are then flagged. The reference antenna is selected to be the un-flagged antenna with the smallest visibility rms.

In [5]:
run pipelines/processMeerKAT/cal_scripts/calc_refant.py --config myconfig.txt

2019-08-07 10:54:14,587 INFO: Flux field scan no: 1
2019-08-07 10:54:14,595 INFO: Antenna statistics on total flux calibrator
2019-08-07 10:54:14,596 INFO: (flux in Jy averaged over scans & channels, and over all of each antenna's baselines)
2019-08-07 10:54:14,597 INFO: ant median rms 
2019-08-07 10:54:48,526 INFO: All 2.25  17.55
2019-08-07 10:54:48,533 INFO: 19  1.57  7.21 (best antenna)
2019-08-07 10:54:48,535 INFO: 1   1.74  8.36 (1st good antenna)
2019-08-07 10:54:48,536 INFO: setting reference antenna to: 19
2019-08-07 10:54:48,538 INFO: Bad antennas: [0, 10, 27, 34, 37, 57, 58, 59, 61, 62]


Show log 2019-08-07 09:54:14	INFO	msmetadata_cmpt.cc::open	Performing internal consistency checks on data/XMMLSS12_1539286252_tiny.ms...
 2019-08-07 09:54:14	INFO	MSMetaData::_computeScanAndSubScanProperties Computing scan and subscan properties...
 2019-08-07 09:54:49	INFO	name::	No table opened.
 2019-08-07 09:54:49	INFO	name::	No table opened.

# Data partition

The input measurement set (MS) is partitioned into a [multi-measurement set (MMS)](https://casa.nrao.edu/casadocs/casa-5.4.1/uv-manipulation/data-partition) using the CASA task `partition`. This task splits up the main MS into smaller SUBMSs that are individual units of a larger logical MMS. The number of SUBMSs created are equal to the number of scans in the input MS. Partitioning the data in this manner allows for more efficient use of computation while using MPI, since each SUBMS can be independently operated on by different MPI workers.

In [6]:
run pipelines/processMeerKAT/cal_scripts/partition.py --config myconfig.txt

Show log 2019-08-07 09:54:49	INFO	msmetadata_cmpt.cc::open	Performing internal consistency checks on data/XMMLSS12_1539286252_tiny.ms...
 2019-08-07 09:54:49	INFO	MSMetaData::_computeScanAndSubScanProperties Computing scan and subscan properties...
 2019-08-07 09:54:49	INFO	partition::::	
 2019-08-07 09:54:49	INFO	partition::::+	##########################################
 2019-08-07 09:54:49	INFO	partition::::+	##### Begin Task: partition #####
 2019-08-07 09:54:49	INFO	partition::::	partition(vis="data/XMMLSS12_1539286252_tiny.ms",outputvis="XMMLSS12_1539286252_tiny.mms",createmms=True,separationaxis="scan",numsubms=42,
 2019-08-07 09:54:49	INFO	partition::::+ flagbackup=True,datacolumn="DATA",field="",spw="0:860~1700MHz",scan="",
 2019-08-07 09:54:49	INFO	partition::::+ antenna="",correlation="",timerange="",intent="",array="",
 2019-08-07 09:54:49	INFO	partition::::+ uvrange="",observation="",feed="",disableparallel=False,ddistart=-1,
 2019-08-07 09:54:49	INFO	partition::::+ taql="")
 2019-08-07 09:54:49	INFO	ParallelDataHelper::::	Analyzing MS for partitioning
 2019-08-07 09:54:51	INFO	partition::::	
 2019-08-07 09:54:51	INFO	partition::::+	##########################################
 2019-08-07 09:54:51	INFO	partition::::+	##### Begin Task: partition #####
 2019-08-07 09:54:51	INFO	partition::::	partition(vis="/scratch/mightee/MeerKAT-IRIS/data/XMMLSS12_1539286252_tiny.ms",outputvis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms.data/XMMLSS12_1539286252_tiny.mms.0000.ms",createmms=False,separationaxis="scan",numsubms=42,
 2019-08-07 09:54:51	INFO	partition::::+ flagbackup=True,datacolumn="DATA",field="",spw="0:860~1700MHz",scan="1",
 2019-08-07 09:54:51	INFO	partition::::+ antenna="",correlation="",timerange="",intent="",array="",
 2019-08-07 09:54:51	INFO	partition::::+ uvrange="",observation="",feed="",disableparallel=False,ddistart=-1,
 2019-08-07 09:54:51	INFO	partition::::+ taql="")
 2019-08-07 09:54:51	INFO	MSTransformManager::parseMsSpecParams	Input file name is /scratch/mightee/MeerKAT-IRIS/data/XMMLSS12_1539286252_tiny.ms
 2019-08-07 09:54:51	INFO	MSTransformManager::parseMsSpecParams	Data column is DATA
 2019-08-07 09:54:51	INFO	MSTransformManager::parseMsSpecParams	Output file name is /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms.data/XMMLSS12_1539286252_tiny.mms.0000.ms
 2019-08-07 09:54:51	INFO	MSTransformManager::parseDataSelParams	scan selection is 1
 2019-08-07 09:54:51	INFO	MSTransformManager::parseDataSelParams	spw selection is 0:860~1700MHz
 2019-08-07 09:54:51	INFO	MSTransformManager::colCheckInfo	Adding DATA column to output MS from input DATA column
 2019-08-07 09:54:51	INFO	MSTransformManager::initDataSelectionParams	Selected Scans Ids are [1]
 2019-08-07 09:54:51	INFO	MSTransformManager::initDataSelectionParams	Selected SPWs Ids are Axis Lengths: [1, 4] (NB: Matrix in Row/Column order)
 2019-08-07 09:54:51	INFO	MSTransformManager::initDataSelectionParams+	[0, 0, 717, 1]
 2019-08-07 09:54:51	INFO	MSTransformManager::open	Select data
 2019-08-07 09:54:51	INFO	MSTransformManager::createOutputMSStructure	Create output MS structure
 2019-08-07 09:54:51	INFO	MSTransformDataHandler::makeSelection	36288 out of 3489696 rows are going to be considered due to the selection criteria.
 2019-08-07 09:54:52	INFO	partition::::	Run the tool to partition the MS
 2019-08-07 09:54:53	INFO	partition::::	##### End Task: partition #####
 2019-08-07 09:54:53	INFO	partition::::+	##########################################
 2019-08-07 09:54:53	INFO	partition::::	
 2019-08-07 09:54:53	INFO	partition::::+	##########################################
 2019-08-07 09:54:53	INFO	partition::::+	##### Begin Task: partition #####
 2019-08-07 09:54:53	INFO	partition::::	partition(vis="/scratch/mightee/MeerKAT-IRIS/data/XMMLSS12_1539286252_tiny.ms",outputvis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms.data/XMMLSS12_1539286252_tiny.mms.0001.ms",createmms=False,separationaxis="scan",numsubms=42,
 20

# Flagging (round 1) 

The first of two rounds of pre-calibration flagging. If `badfreqranges` and `badants` are specified in the config file, they are flagged. These lists are also allowed to be empty. Further, any autocorrelations are also flagged using `mode='manual'` and `autocorr=True` in the flagdata parameters. 

Subsequently, `flagdata` is called on the calibrators and target sources with conservative limits to clip out the worst RFI (the data are clipped at the level of 50 Jy). It also makes a single call to `tfcrop` to flag data at a 6 $\sigma$ limit. `tfcrop` in this case is preferred, since the as yet uncalibrated bandpass shape should be taken care of by fitting a piecewise polynomial across the band.

In [7]:
run pipelines/processMeerKAT/cal_scripts/flag_round_1.py --config myconfig.txt

Show log 2019-08-07 10:01:53	INFO	flagdata::::	
 2019-08-07 10:01:53	INFO	flagdata::::+	##########################################
 2019-08-07 10:01:53	INFO	flagdata::::+	##### Begin Task: flagdata #####
 2019-08-07 10:01:53	INFO	flagdata::::	flagdata(vis="XMMLSS12_1539286252_tiny.mms",mode="manual",autocorr=False,inpfile="",reason="any",
 2019-08-07 10:01:53	INFO	flagdata::::+ tbuff=0.0,spw="0:935~947MHz",field="",antenna="",uvrange="",
 2019-08-07 10:01:53	INFO	flagdata::::+ timerange="",correlation="",scan="",intent="",array="",
 2019-08-07 10:01:53	INFO	flagdata::::+ observation="",feed="",clipminmax=[],datacolumn="DATA",clipoutside=True,
 2019-08-07 10:01:53	INFO	flagdata::::+ channelavg=False,chanbin=1,timeavg=False,timebin="0s",clipzeros=False,
 2019-08-07 10:01:53	INFO	flagdata::::+ quackinterval=1.0,quackmode="beg",quackincrement=False,tolerance=0.0,addantenna="",
 2019-08-07 10:01:53	INFO	flagdata::::+ lowerlimit=0.0,upperlimit=90.0,ntime="scan",combinescans=False,timecutoff=4.0,
 2019-08-07 10:01:53	INFO	flagdata::::+ freqcutoff=3.0,timefit="line",freqfit="poly",maxnpieces=7,flagdimension="freqtime",
 2019-08-07 10:01:53	INFO	flagdata::::+ usewindowstats="none",halfwin=1,extendflags=True,winsize=3,timedev="",
 2019-08-07 10:01:53	INFO	flagdata::::+ freqdev="",timedevscale=5.0,freqdevscale=5.0,spectralmax=1000000.0,spectralmin=0.0,
 2019-08-07 10:01:53	INFO	flagdata::::+ antint_ref_antenna="",minchanfrac=0.6,verbose=False,extendpols=True,growtime=50.0,
 2019-08-07 10:01:53	INFO	flagdata::::+ growfreq=50.0,growaround=False,flagneartime=False,flagnearfreq=False,minrel=0.0,
 2019-08-07 10:01:53	INFO	flagdata::::+ maxrel=1.0,minabs=0,maxabs=-1,spwchan=False,spwcorr=False,
 2019-08-07 10:01:53	INFO	flagdata::::+ basecnt=False,fieldcnt=False,name="Summary",action="apply",display="",
 2019-08-07 10:01:53	INFO	flagdata::::+ flagbackup=True,savepars=False,cmdreason="",outfile="",overwrite=True,
 2019-08-07 10:01:53	INFO	flagdata::::+ writeflags=True)
 2019-08-07 10:01:53	INFO	flagdata::::	Backup original flags before applying new flags
 2019-08-07 10:01:53	INFO	AgentFlagger::open	Table type is Measurement Set
 2019-08-07 10:01:53	INFO	FlagVersion::saveFlagVersion	Creating new backup flag file called flagdata_1
 2019-08-07 10:02:12	INFO	flagdata::::	
 2019-08-07 10:02:12	INFO	flagdata::::+	##########################################
 2019-08-07 10:02:12	INFO	flagdata::::+	##### Begin Task: flagdata #####
 2019-08-07 10:02:12	INFO	flagdata::::	flagdata(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",mode="manual",autocorr=False,inpfile="",reason="any",
 2019-08-07 10:02:12	INFO	flagdata::::+ tbuff=0.0,spw="0:935~947MHz",field="",antenna="",uvrange="",
 2019-08-07 10:02:12	INFO	flagdata::::+ timerange="",correlation="",scan="",intent="",array="",
 2019-08-07 10:02:12	INFO	flagdata::::+ observation="",feed="",clipminmax=[],datacolumn="DATA",clipoutside=True,
 2019-08-07 10:02:12	INFO	flagdata::::+ channelavg=False,chanbin=1,timeavg=False,timebin="0s",clipzeros=False,
 2019-08-07 10:02:12	INFO	flagdata::::+ quackinterval=1.0,quackmode="beg",quackincrement=False,tolerance=0.0,addantenna="",
 2019-08-07 10:02:12	INFO	flagdata::::+ lowerlimit=0.0,upperlimit=90.0,ntime="scan",combinescans=False,timecutoff=4.0,
 2019-08-07 10:02:12	INFO	flagdata::::+ freqcutoff=3.0,timefit="line",freqfit="poly",maxnpieces=7,flagdimension="freqtime",
 2019-08-07 10:02:12	INFO	flagdata::::+ usewindowstats="none",halfwin=1,extendflags=True,winsize=3,timedev="",
 2019-08-07 10:02:12	INFO	flagdata::::+ freqdev="",timedevscale=5.0,freqdevscale=5.0,spectralmax=1000000.0,spectralmin=0.0,
 2019-08-07 10:02:12	INFO	flagdata::::+ antint_ref_antenna="",minchanfrac=0.6,verbose=False,extendpols=True,growtime=50.0,
 2019-08-07 10:02:12	INFO	flagdata::::+ growfreq=50.0,growaround=False,flagneartime=False,flagnearfreq=False,minrel=0.0,
 2019-08-07 10:02:12	INFO	flagdata::::+ maxrel=1.0,minabs=0,maxabs=-1,spwch

# setjy 

The `setjy` task is run on the specified primary calibrators - this step is run once each before the first and second rounds of calibration.

By default, the ‘Perley-Butler 2010’ flux scale is used, since it is the only one which contains the popular southern calibrator PKS B1934-638. In case the calibrator J0408-6545 is present in the data, it is preferred. A broadband Stokes I model for J0408-6545 is used, via the `manual` mode of `setjy`.

In [8]:
run pipelines/processMeerKAT/cal_scripts/setjy.py --config myconfig.txt

Show log 2019-08-07 10:47:40	INFO	clearcal::::	
 2019-08-07 10:47:40	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:40	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 10:47:40	INFO	clearcal::::	clearcal(vis="XMMLSS12_1539286252_tiny.mms",field="",spw="",intent="",addmodel=False)
 2019-08-07 10:47:40	INFO	clearcal::::	
 2019-08-07 10:47:40	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:40	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 10:47:40	INFO	clearcal::::	clearcal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",field="",spw="",intent="",addmodel=False)
 2019-08-07 10:47:40	INFO	clearcal::::	Need to create scratch columns; ignoring selection.
 2019-08-07 10:47:40	WARN	calibrater::setvi(bool,bool)	Forcing use of OLD VisibilityIterator.
 2019-08-07 10:47:40	INFO	calibrater::open	****Using OLD VI-driven calibrater tool****
 2019-08-07 10:47:40	INFO	calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms for calibration.
 2019-08-07 10:47:40	INFO	VisSetUtil::addScrCols	Adding CORRECTED_DATA column(s).
 2019-08-07 10:47:41	INFO	VisSetUtil::addScrCols	Start copying column keyword(s) of CORRECTED_DATA from DATA
 2019-08-07 10:47:41	INFO	Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 10:47:41	INFO	clearcal::::	CASA Version 5.5.0-149 
 2019-08-07 10:47:41	INFO	clearcal::::	
 2019-08-07 10:47:41	INFO	clearcal::::	##### End Task: clearcal #####
 2019-08-07 10:47:41	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:41	INFO	clearcal::::	
 2019-08-07 10:47:41	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:41	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 10:47:41	INFO	clearcal::::	clearcal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0001.ms",field="",spw="",intent="",addmodel=False)
 2019-08-07 10:47:41	INFO	clearcal::::	Need to create scratch columns; ignoring selection.
 2019-08-07 10:47:41	WARN	calibrater::setvi(bool,bool)	Forcing use of OLD VisibilityIterator.
 2019-08-07 10:47:41	INFO	calibrater::open	****Using OLD VI-driven calibrater tool****
 2019-08-07 10:47:41	INFO	calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0001.ms for calibration.
 2019-08-07 10:47:41	INFO	VisSetUtil::addScrCols	Adding CORRECTED_DATA column(s).
 2019-08-07 10:47:45	INFO	VisSetUtil::addScrCols	Start copying column keyword(s) of CORRECTED_DATA from DATA
 2019-08-07 10:47:45	INFO	Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 10:47:45	INFO	clearcal::::	CASA Version 5.5.0-149 
 2019-08-07 10:47:45	INFO	clearcal::::	
 2019-08-07 10:47:45	INFO	clearcal::::	##### End Task: clearcal #####
 2019-08-07 10:47:45	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:45	INFO	clearcal::::	
 2019-08-07 10:47:45	INFO	clearcal::::+	##########################################
 2019-08-07 10:47:45	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 10:47:45	INFO	clearcal::::	clearcal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0002.ms",field="",spw="",intent="",addmodel=False)
 2019-08-07 10:47:45	INFO	clearcal::::	Need to create scratch columns; ignoring selection.
 2019-08-07 10:47:45	WARN	calibrater::setvi(bool,bool)	Forcing use of OLD VisibilityIterator.
 2019-08-07 10:47:45	INFO	calibrater::open	****Using OLD VI-driven calibrater tool****
 2019-08-07 10:47:45	INFO	calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0002.ms for calibration.
 2019-08-07 10:47:45	INFO	VisSetUtil::addScrCols	Adding CORRECTED_DATA column

# Parallel hand calibration 

Standard delay, bandpass and gain calibration is run on the data, in order to obtain better statistics for a second round of flagging.

In [9]:
run pipelines/processMeerKAT/cal_scripts/xx_yy_solve.py --config myconfig.txt

2019-08-07 12:00:37,307 INFO:  starting antenna-based delay (kcorr)
 -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal
2019-08-07 12:02:21,277 INFO:  starting bandpass -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal
2019-08-07 12:02:53,597 INFO:  starting gain calibration
 -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.gcal


Show log 2019-08-07 11:00:37	INFO	gaincal::::	
 2019-08-07 11:00:37	INFO	gaincal::::+	##########################################
 2019-08-07 11:00:37	INFO	gaincal::::+	##### Begin Task: gaincal #####
 2019-08-07 11:00:37	INFO	gaincal::::	gaincal(vis="XMMLSS12_1539286252_tiny.mms",caltable="/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal",field="2",spw="",intent="",
 2019-08-07 11:00:37	INFO	gaincal::::+ selectdata=True,timerange="",uvrange="",antenna="",scan="",
 2019-08-07 11:00:37	INFO	gaincal::::+ observation="",msselect="",solint="inf",combine="",preavg=-1.0,
 2019-08-07 11:00:37	INFO	gaincal::::+ refant="19",refantmode="flex",minblperant=4,minsnr=3.0,solnorm=False,
 2019-08-07 11:00:37	INFO	gaincal::::+ normtype="mean",gaintype="K",smodel=[],calmode="ap",solmode="",
 2019-08-07 11:00:37	INFO	gaincal::::+ rmsthresh=[],append=False,splinetime=3600.0,npointaver=3,phasewrap=180.0,
 2019-08-07 11:00:37	INFO	gaincal::::+ docallib=False,callib="",gaintable=[''],gainfield=[''],interp=[],
 2019-08-07 11:00:37	INFO	gaincal::::+ spwmap=[],parang=False)
 2019-08-07 11:00:37	INFO	gaincal::calibrater::open	****Using NEW VI2-driven calibrater tool****
 2019-08-07 11:00:37	INFO	gaincal::calibrater::open	Opening MS: XMMLSS12_1539286252_tiny.mms for calibration.
 2019-08-07 11:00:37	INFO	gaincal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 11:00:37	INFO	gaincal::::	NB: gaincal automatically excludes auto-correlations.
 2019-08-07 11:00:37	INFO	calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 11:00:37	INFO	calibrater::reset	Reseting solve/apply state
 2019-08-07 11:00:37	INFO	Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 11:00:37	INFO	Calibrater::selectvis+ Selecting on field: '2'
 2019-08-07 11:00:37	INFO	Calibrater::selectvis+ Selecting with TaQL: 'ANTENNA1!=ANTENNA2'
 2019-08-07 11:00:37	INFO	Calibrater::selectvis	By selection 3489696 rows are reduced to 439425
 2019-08-07 11:00:37	INFO	Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 11:00:37	INFO	calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/s' mStep='0km/s' msSelect='ANTENNA1!=ANTENNA2'
 2019-08-07 11:00:37	INFO	calibrater::setsolve	Beginning setsolve--(MSSelection version)-------
 2019-08-07 11:00:37	INFO	Calibrater::setsolve	Arranging to SOLVE:
 2019-08-07 11:00:38	INFO	Calibrater::setsolve	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal append=false solint=inf refantmode='flex' refant='m020' minsnr=3 apmode=AP solnorm=false
 2019-08-07 11:00:38	INFO	calibrater::solve	Beginning solve-----------------------------
 2019-08-07 11:00:38	INFO	Calibrater::solve	The following calibration terms are arranged for apply:
 2019-08-07 11:00:38	INFO	Calibrater::solve	. (None)
 2019-08-07 11:00:38	INFO	Calibrater::solve	The following calibration term is arranged for solve:
 2019-08-07 11:00:38	INFO	Calibrater::solve	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal append=false solint=inf refantmode='flex' refant='m020' minsnr=3 apmode=AP solnorm=false
 2019-08-07 11:00:38	INFO	Calibrater::solve	For solint = inf, found 18 solution intervals.
 2019-08-07 11:02:21	INFO	Calibrater::solve Found good K Jones solutions in 18 solution intervals.
 2019-08-07 11:02:21	INFO Writing solutions to table: /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal
 2019-08-07 11:02:21	INFO	calibrater::solve	Finished solving.
 2019-08-07 11:02:21	INFO	gaincal::::	Calibration solve statistics per spw: (expected/attempted/succeeded):
 2019-08-07 11:02:21	INFO	gaincal:::: Spw 0: 18/18/18
 2019-08-07 11:02:21	INFO	gaincal::::	##### End Task: gaincal #####
 2019-08-07 11:02:21	INFO	gaincal::::+	##########################################
 2019-08-07 11:02:21	INFO	bandpass::::	
 2019-08-07 11:02:21	INFO	bandpass::::+	##########################################
 2

In [10]:
run pipelines/processMeerKAT/cal_scripts/xx_yy_apply.py --config myconfig.txt

2019-08-07 12:05:11,566 INFO:  applying calibration -> primary calibrator


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

2019-08-07 12:05:38,549 INFO:  applying calibration -> secondary calibrator


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

2019-08-07 12:07:14,529 INFO:  applying calibration -> target calibrator


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

Hide log 2019-08-07 11:05:12	INFO	applycal::::	
 2019-08-07 11:05:12	INFO	applycal::::+	##########################################
 2019-08-07 11:05:12	INFO	applycal::::+	##### Begin Task: applycal #####
 2019-08-07 11:05:12	INFO	applycal::::	applycal(vis="XMMLSS12_1539286252_tiny.mms",field="0",spw="",intent="",selectdata=False,
 2019-08-07 11:05:12	INFO	applycal::::+ timerange="",uvrange="",antenna="",scan="",observation="",
 2019-08-07 11:05:12	INFO	applycal::::+ msselect="",docallib=False,callib="",gaintable=['/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.fluxscale'],gainfield=['2', '0', '0'],
 2019-08-07 11:05:12	INFO	applycal::::+ interp=[],spwmap=[],calwt=False,parang=True,applymode="",
 2019-08-07 11:05:12	INFO	applycal::::+ flagbackup=True)
 2019-08-07 11:05:12	INFO	applycal::AgentFlagger::open	Table type is Measurement Set
 2019-08-07 11:05:12	INFO	FlagVersion::saveFlagVersion	Creating new backup flag file called applycal_1
 2019-08-07 11:05:21	INFO	applycal::::	
 2019-08-07 11:05:21	INFO	applycal::::+	##########################################
 2019-08-07 11:05:21	INFO	applycal::::+	##### Begin Task: applycal #####
 2019-08-07 11:05:21	INFO	applycal::::	applycal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",field="0",spw="",intent="",selectdata=False,
 2019-08-07 11:05:21	INFO	applycal::::+ timerange="",uvrange="",antenna="",scan="",observation="",
 2019-08-07 11:05:21	INFO	applycal::::+ msselect="",docallib=False,callib="",gaintable=['/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.fluxscale'],gainfield=['2', '0', '0'],
 2019-08-07 11:05:21	INFO	applycal::::+ interp=[],spwmap=[],calwt=[False],parang=True,applymode="",
 2019-08-07 11:05:21	INFO	applycal::::+ flagbackup=False)
 2019-08-07 11:05:21	INFO	applycal::calibrater::open	****Using NEW VI2-driven calibrater tool****
 2019-08-07 11:05:21	INFO	applycal::calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms for calibration.
 2019-08-07 11:05:21	INFO	applycal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 11:05:21	INFO	applycal::calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 11:05:21	INFO	applycal::calibrater::reset	Reseting solve/apply state
 2019-08-07 11:05:21	INFO	applycal::Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 11:05:21	INFO	applycal::Calibrater::selectvis+ Selecting on field: '0'
 2019-08-07 11:05:21	INFO	applycal::Calibrater::selectvis	Selection did not drop any rows
 2019-08-07 11:05:21	INFO	applycal::Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 11:05:21	INFO	applycal::calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/s' mStep='0km/s' msSelect=''
 2019-08-07 11:05:21	INFO	applycal::calibrater::setapply	Beginning setapply--(MSSelection version)-------
 2019-08-07 11:05:21	INFO	applycal::Calibrater::setapply(type, applypar)	Arranging to APPLY:
 2019-08-07 11:05:21	INFO	applycal::Calibrater::setapply(type, applypar)	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal select= interp=linear spwmap=[-1] calWt=false
 2019-08-07 11:05:21	INFO	applycal::calibrater::setapply	Beginning setapply--(MSSelection version)-------
 2019-08-07 11:05:21	INFO	applycal::Calibrater::setapply(type, applypar)	Arranging to APPLY:
 2019-08-07 11:05:21	INFO	applycal::Calibrater::setapply(type, applypar)	. B Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal select= interp=linear,linear spwmap=[-1] ca

# Flagging (round 2) 

Similar to the first round, the `tfcrop` algorithm is run independently on the primary and secondary calibrator and the target(s). The thresholds are lower than the first round as the algorithm is now operating on calibrated data.

In [11]:
run pipelines/processMeerKAT/cal_scripts/flag_round_2.py --config myconfig.txt

Show log 2019-08-07 11:16:04	INFO	flagdata::::	
 2019-08-07 11:16:04	INFO	flagdata::::+	##########################################
 2019-08-07 11:16:04	INFO	flagdata::::+	##### Begin Task: flagdata #####
 2019-08-07 11:16:04	INFO	flagdata::::	flagdata(vis="XMMLSS12_1539286252_tiny.mms",mode="clip",autocorr=False,inpfile="",reason="any",
 2019-08-07 11:16:04	INFO	flagdata::::+ tbuff=0.0,spw="",field="0",antenna="",uvrange="",
 2019-08-07 11:16:04	INFO	flagdata::::+ timerange="",correlation="",scan="",intent="",array="",
 2019-08-07 11:16:04	INFO	flagdata::::+ observation="",feed="",clipminmax=[0.0, 50.0],datacolumn="corrected",clipoutside=True,
 2019-08-07 11:16:04	INFO	flagdata::::+ channelavg=False,chanbin=1,timeavg=False,timebin="0s",clipzeros=True,
 2019-08-07 11:16:04	INFO	flagdata::::+ quackinterval=1.0,quackmode="beg",quackincrement=False,tolerance=0.0,addantenna="",
 2019-08-07 11:16:04	INFO	flagdata::::+ lowerlimit=0.0,upperlimit=90.0,ntime="scan",combinescans=False,timecutoff=4.0,
 2019-08-07 11:16:04	INFO	flagdata::::+ freqcutoff=3.0,timefit="line",freqfit="poly",maxnpieces=7,flagdimension="freqtime",
 2019-08-07 11:16:04	INFO	flagdata::::+ usewindowstats="none",halfwin=1,extendflags=True,winsize=3,timedev="",
 2019-08-07 11:16:04	INFO	flagdata::::+ freqdev="",timedevscale=5.0,freqdevscale=5.0,spectralmax=1000000.0,spectralmin=0.0,
 2019-08-07 11:16:04	INFO	flagdata::::+ antint_ref_antenna="",minchanfrac=0.6,verbose=False,extendpols=False,growtime=50.0,
 2019-08-07 11:16:04	INFO	flagdata::::+ growfreq=50.0,growaround=False,flagneartime=False,flagnearfreq=False,minrel=0.0,
 2019-08-07 11:16:04	INFO	flagdata::::+ maxrel=1.0,minabs=0,maxabs=-1,spwchan=False,spwcorr=False,
 2019-08-07 11:16:04	INFO	flagdata::::+ basecnt=False,fieldcnt=False,name="Summary",action="apply",display="",
 2019-08-07 11:16:04	INFO	flagdata::::+ flagbackup=True,savepars=False,cmdreason="",outfile="",overwrite=True,
 2019-08-07 11:16:04	INFO	flagdata::::+ writeflags=True)
 2019-08-07 11:16:04	INFO	flagdata::::	Backup original flags before applying new flags
 2019-08-07 11:16:04	INFO	AgentFlagger::open	Table type is Measurement Set
 2019-08-07 11:16:04	INFO	FlagVersion::saveFlagVersion	Creating new backup flag file called flagdata_14
 2019-08-07 11:16:22	INFO	flagdata::::	
 2019-08-07 11:16:22	INFO	flagdata::::+	##########################################
 2019-08-07 11:16:22	INFO	flagdata::::+	##### Begin Task: flagdata #####
 2019-08-07 11:16:22	INFO	flagdata::::	flagdata(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",mode="clip",autocorr=False,inpfile="",reason="any",
 2019-08-07 11:16:22	INFO	flagdata::::+ tbuff=0.0,spw="",field="0",antenna="",uvrange="",
 2019-08-07 11:16:22	INFO	flagdata::::+ timerange="",correlation="",scan="",intent="",array="",
 2019-08-07 11:16:22	INFO	flagdata::::+ observation="",feed="",clipminmax=[0.0, 50.0],datacolumn="corrected",clipoutside=True,
 2019-08-07 11:16:22	INFO	flagdata::::+ channelavg=False,chanbin=1,timeavg=False,timebin="0s",clipzeros=True,
 2019-08-07 11:16:22	INFO	flagdata::::+ quackinterval=1.0,quackmode="beg",quackincrement=False,tolerance=0.0,addantenna="",
 2019-08-07 11:16:22	INFO	flagdata::::+ lowerlimit=0.0,upperlimit=90.0,ntime="scan",combinescans=False,timecutoff=4.0,
 2019-08-07 11:16:22	INFO	flagdata::::+ freqcutoff=3.0,timefit="line",freqfit="poly",maxnpieces=7,flagdimension="freqtime",
 2019-08-07 11:16:22	INFO	flagdata::::+ usewindowstats="none",halfwin=1,extendflags=True,winsize=3,timedev="",
 2019-08-07 11:16:22	INFO	flagdata::::+ freqdev="",timedevscale=5.0,freqdevscale=5.0,spectralmax=1000000.0,spectralmin=0.0,
 2019-08-07 11:16:22	INFO	flagdata::::+ antint_ref_antenna="",minchanfrac=0.6,verbose=False,extendpols=False,growtime=50.0,
 2019-08-07 11:16:22	INFO	flagdata::::+ growfreq=50.0,growaround=False,flagneartime=False,flagnearfreq=False,minrel=0.0,
 2019-08-07 11:16:22	INFO	flagdata::::+ maxrel=1.0,minabs=0,maxabs=-1,sp

In [12]:
run pipelines/processMeerKAT/cal_scripts/setjy.py --config myconfig.txt

Show log 2019-08-07 12:34:51	INFO	clearcal::::	
 2019-08-07 12:34:51	INFO	clearcal::::+	##########################################
 2019-08-07 12:34:51	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 12:34:51	INFO	clearcal::::	clearcal(vis="XMMLSS12_1539286252_tiny.mms",field="",spw="",intent="",addmodel=False)
 2019-08-07 12:34:51	INFO	clearcal::::	
 2019-08-07 12:34:51	INFO	clearcal::::+	##########################################
 2019-08-07 12:34:51	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 12:34:51	INFO	clearcal::::	clearcal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",field="",spw="",intent="",addmodel=False)
 2019-08-07 12:34:51	WARN	clearcal::calibrater::setvi(bool,bool)	Forcing use of OLD VisibilityIterator.
 2019-08-07 12:34:51	INFO	clearcal::calibrater::open	****Using OLD VI-driven calibrater tool****
 2019-08-07 12:34:51	INFO	clearcal::calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms for calibration.
 2019-08-07 12:34:51	INFO	clearcal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 12:34:51	INFO	clearcal::calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 12:34:51	INFO	clearcal::calibrater::reset	Reseting solve/apply state
 2019-08-07 12:34:51	INFO	clearcal::Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 12:34:51	INFO	clearcal::Calibrater::selectvis	Selection did not drop any rows
 2019-08-07 12:34:51	INFO	clearcal::Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 12:34:51	INFO	clearcal::calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/s' mStep='0km/s' msSelect=''
 2019-08-07 12:34:51	INFO	clearcal::::	Clearing all model records in MS header.
 2019-08-07 12:34:51	INFO	clearcal:::: J1939-6342 (id = 0) deleted.
 2019-08-07 12:34:51	INFO	clearcal::calibrater::initcalset	Beginning initcalset------------------------
 2019-08-07 12:34:51	INFO	clearcal::VisSet::VisSet	Initializing MODEL_DATA (to unity) and CORRECTED_DATA (to DATA)
 2019-08-07 12:34:53	INFO	clearcal::VisSet::VisSet	Initialized 36288 rows.
 2019-08-07 12:34:53	INFO	clearcal::::	CASA Version 5.5.0-149 
 2019-08-07 12:34:53	INFO	clearcal::::	
 2019-08-07 12:34:53	INFO	clearcal::::	##### End Task: clearcal #####
 2019-08-07 12:34:53	INFO	clearcal::::+	##########################################
 2019-08-07 12:34:53	INFO	clearcal::::	
 2019-08-07 12:34:53	INFO	clearcal::::+	##########################################
 2019-08-07 12:34:53	INFO	clearcal::::+	##### Begin Task: clearcal #####
 2019-08-07 12:34:53	INFO	clearcal::::	clearcal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0001.ms",field="",spw="",intent="",addmodel=False)
 2019-08-07 12:34:53	WARN	clearcal::calibrater::setvi(bool,bool)	Forcing use of OLD VisibilityIterator.
 2019-08-07 12:34:53	INFO	clearcal::calibrater::open	****Using OLD VI-driven calibrater tool****
 2019-08-07 12:34:53	INFO	clearcal::calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0001.ms for calibration.
 2019-08-07 12:34:53	INFO	clearcal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 12:34:53	INFO	clearcal::calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 12:34:53	INFO	clearcal::calibrater::reset	Reseting solve/apply state
 2019-08-07 12:34:53	INFO	clearcal::Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 12:34:53	INFO	clearcal::Calibrater::selectvis	Selection did not drop any rows
 2019-08-07 12:34:53	INFO	clearcal::Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 12:34:53	INFO	clearcal::calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/

# Cross hand calibration 

The full Stokes calibration procedure is done across as much of the SPW as is requested in the config file. In the default case, the entire SPW (spanning ~ 800 MHz) is calibrated across. The caveat here is that CASA does not support a true wideband, full polarization calibration. For example the Stokes Q and U values of a source with non-zero RM across the band will not be correctly accounted for. The assumption CASA makes is that the bandwidth is split into several smaller SPWs (such as is the case of VLA or ALMA) and that the Stokes parameters within each SPW can be assumed to be a constant. We have identified work-arounds to this, and will be implementing the fix in upcoming versions of the pipeline.

The cross-hand calibration performs the following steps:
* Delay calibration (the K term), time averaged, parallel hand
* Bandpass calibration (the B term), time averaged, parallel hand
* Cross hand delay calibration (the KCROSS term), time averaged, cross hand

After the cross-hand delay calibration is performed, we iterate over calculating the time dependent gains. Initially the time-dependent gains are calculated for the primary and secondary calibrators, as a function of time and parallactic angle. The polarization properties of the secondary are assumed to be unknown, and are determined from the gain variation as a function of parallactic angle. This is fit for by the `qufromgain` task, which is contained in `almapolhelpers` and can be accessed in CASA by

```
from almapolhelpers import *
```

This imports several helper tasks that are meant to solve ALMA polarization, but are general enough to work with any telescope that has linear feeds.

Once the fractional Q and U values are determined for the phase calibrator, the gain solutions are recomputed with the fractional polarization as an input, in theory resulting in more accurate gain solutions. This is followed by a call to `xyamb`, also within `almapolhelpers` that breaks the ambiguity in the X-Y phases for the solutions generated by `qufromgain`. These can be cross-checked with the solutions obtained by running `gaincal` with `gaintype='XYf+QU'` which solves for the X-Y phase as a function of frequency, assuming an unknown source Q, U value. Finally we run `polcal` in the `Dflls` mode in order to calculate the polarization leakage (the D term) as a function of frequency (f), using a linear least squares algorithm (lls). Finally, we bootstrap the fluxes from the primary to the secondary using `fluxscale`.

In [13]:
run pipelines/processMeerKAT/cal_scripts/xy_yx_solve.py --config myconfig.txt

2019-08-07 13:44:46,377 INFO:  starting antenna-based delay (kcorr)
 -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal
2019-08-07 13:46:31,880 INFO:  starting bandpass -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal
2019-08-07 13:47:03,272 INFO:  starting cross hand delay -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.xdel
2019-08-07 13:49:10,547 INFO:  starting gaincal -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.mms.g1cal
2019-08-07 13:52:16,610 INFO: 
 Solve for Q, U from initial gain solution
2019-08-07 13:52:16,748 INFO: (-0.012887761252330349, -0.031960989042421978)
2019-08-07 13:52:16,750 INFO: 
 Starting x-y phase calibration
 -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.mms.xyambcal


Latitude =  -30.7124007766
Found as many as 4 fields.
Can't discern an ALMA bandname from: none
Found as many as 1 spws.
Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
Fld= 0 Spw= 0 Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
(B=none, PA offset=0.0deg) Gx/Gy= 1.00766914578 Q= 0.00511203916839 U= -0.00186378425788 P= 0.00544119804998 X= -10.0156051604
For field id =  0  there are  1 good spws.
Spw mean: Fld= 0 Q= 0.00511203916839 U= -0.00186378425788 (rms= 0.0 0.0 ) P= 0.00544119804998 X= -10.0156051604
Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
Fld= 2 Spw= 0 Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
(B=none, PA offset=0.0deg) Gx/Gy= 0.998190111509 Q= -0.0128877612523 U= -0.0319609890424 P= 0.0344615613498 X= -55.9804868374
For field id =  2  there are  1 goo

2019-08-07 13:54:51,488 INFO: 
 Check for x-y phase ambiguity.
2019-08-07 13:54:51,573 INFO: Model for polarization calibrator S = [1.0
2019-08-07 13:54:51,575 INFO: Fractional polarization = 0.03446


Expected QU =  (-0.012887761252330349, -0.031960989042421978)
Spw = 0: Found QU = [ 0.01388603  0.03897931]
   ...CONVERTING X-Y phase from -13.0793966761 to 166.920603324 deg
Ambiguity resolved (spw mean): Q= -0.0138860289007 U= -0.0389793068171 (rms= 0.0 0.0 ) P= 0.0413788370858 X= -54.8039929247
Returning the following Stokes vector: [1.0, -0.013886028900742531, -0.038979306817054749, 0.0]


2019-08-07 13:55:24,769 INFO: 
 solution for secondary with parang = true
2019-08-07 13:58:01,459 INFO: 
 now re-solve for Q,U from the new gainfile
 -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.gcal
2019-08-07 13:58:01,592 INFO: (-0.0015349984966918217, -0.0056420298192221725)
2019-08-07 13:58:01,593 INFO: starting 'Dflls' polcal -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.pcal


Latitude =  -30.7124007766
Found as many as 4 fields.
Can't discern an ALMA bandname from: none
Found as many as 1 spws.
Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
Fld= 0 Spw= 0 Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
(B=none, PA offset=0.0deg) Gx/Gy= 1.00766914578 Q= 0.00511203916839 U= -0.00186378425788 P= 0.00544119804998 X= -10.0156051604
For field id =  0  there are  1 good spws.
Spw mean: Fld= 0 Q= 0.00511203916839 U= -0.00186378425788 (rms= 0.0 0.0 ) P= 0.00544119804998 X= -10.0156051604
Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
Fld= 2 Spw= 0 Can't discern an ALMA bandname from: none
Unresolved bandname: default band position angle set to 0.0
(B=none, PA offset=0.0deg) Gx/Gy= 0.996432925595 Q= -0.00153499849669 U= -0.00564202981922 P= 0.00584711218174 X= -52.609895528
For field id =  2  there are  1 g

2019-08-07 14:00:56,948 INFO:  starting fluxscale -> /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.fluxscale


Show log 2019-08-07 12:44:46	INFO	gaincal::::	
 2019-08-07 12:44:46	INFO	gaincal::::+	##########################################
 2019-08-07 12:44:46	INFO	gaincal::::+	##### Begin Task: gaincal #####
 2019-08-07 12:44:46	INFO	gaincal::::	gaincal(vis="XMMLSS12_1539286252_tiny.mms",caltable="/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal",field="2",spw="",intent="",
 2019-08-07 12:44:46	INFO	gaincal::::+ selectdata=True,timerange="",uvrange="",antenna="",scan="",
 2019-08-07 12:44:46	INFO	gaincal::::+ observation="",msselect="",solint="10min",combine="scan",preavg=-1.0,
 2019-08-07 12:44:46	INFO	gaincal::::+ refant="19",refantmode="flex",minblperant=4,minsnr=3.0,solnorm=False,
 2019-08-07 12:44:46	INFO	gaincal::::+ normtype="mean",gaintype="K",smodel=[],calmode="ap",solmode="",
 2019-08-07 12:44:46	INFO	gaincal::::+ rmsthresh=[],append=False,splinetime=3600.0,npointaver=3,phasewrap=180.0,
 2019-08-07 12:44:46	INFO	gaincal::::+ docallib=False,callib="",gaintable=[''],gainfield=[''],interp=[],
 2019-08-07 12:44:46	INFO	gaincal::::+ spwmap=[],parang=False)
 2019-08-07 12:44:46	INFO	gaincal::calibrater::open	****Using NEW VI2-driven calibrater tool****
 2019-08-07 12:44:46	INFO	gaincal::calibrater::open	Opening MS: XMMLSS12_1539286252_tiny.mms for calibration.
 2019-08-07 12:44:46	INFO	gaincal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 12:44:46	INFO	gaincal::::	NB: gaincal automatically excludes auto-correlations.
 2019-08-07 12:44:46	INFO	calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 12:44:46	INFO	calibrater::reset	Reseting solve/apply state
 2019-08-07 12:44:46	INFO	Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 12:44:46	INFO	Calibrater::selectvis+ Selecting on field: '2'
 2019-08-07 12:44:46	INFO	Calibrater::selectvis+ Selecting with TaQL: 'ANTENNA1!=ANTENNA2'
 2019-08-07 12:44:47	INFO	Calibrater::selectvis	By selection 3489696 rows are reduced to 439425
 2019-08-07 12:44:47	INFO	Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 12:44:47	INFO	calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/s' mStep='0km/s' msSelect='ANTENNA1!=ANTENNA2'
 2019-08-07 12:44:47	INFO	calibrater::setsolve	Beginning setsolve--(MSSelection version)-------
 2019-08-07 12:44:47	INFO	Calibrater::setsolve	Arranging to SOLVE:
 2019-08-07 12:44:47	INFO	Calibrater::setsolve	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal append=false solint=10min refantmode='flex' refant='m020' minsnr=3 apmode=AP solnorm=false
 2019-08-07 12:44:47	INFO	calibrater::solve	Beginning solve-----------------------------
 2019-08-07 12:44:47	INFO	Calibrater::solve	The following calibration terms are arranged for apply:
 2019-08-07 12:44:47	INFO	Calibrater::solve	. (None)
 2019-08-07 12:44:47	INFO	Calibrater::solve	The following calibration term is arranged for solve:
 2019-08-07 12:44:47	INFO	Calibrater::solve	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal append=false solint=10min refantmode='flex' refant='m020' minsnr=3 apmode=AP solnorm=false
 2019-08-07 12:44:47	INFO	Calibrater::solve	For solint = 10min, found 18 solution intervals.
 2019-08-07 12:46:32	INFO	Calibrater::solve Found good K Jones solutions in 18 solution intervals.
 2019-08-07 12:46:32	INFO Writing solutions to table: /scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal
 2019-08-07 12:46:32	INFO	calibrater::solve	Finished solving.
 2019-08-07 12:46:32	INFO	gaincal::::	Calibration solve statistics per spw: (expected/attempted/succeeded):
 2019-08-07 12:46:32	INFO	gaincal:::: Spw 0: 18/18/18
 2019-08-07 12:46:32	INFO	gaincal::::	##### End Task: gaincal #####
 2019-08-07 12:46:32	INFO	gaincal::::+	##########################################
 2019-08-07 12:46:32	INFO	bandpass::::	
 2019-08-07 12:46:32	INFO	bandpass::::+	#################################

In [14]:
run pipelines/processMeerKAT/cal_scripts/xy_yx_apply.py --config myconfig.txt

2019-08-07 14:00:57,679 INFO: applying calibrations: primary calibrator


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

2019-08-07 14:01:34,177 INFO:  applying calibrations: secondary calibrators


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

2019-08-07 14:03:53,424 INFO:  applying calibrations: target fields


*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The selected table has zero rows.
*** Error *** Error in data selection specification: MSSelectionNullSelection : The sele

Hide log 2019-08-07 13:00:58	INFO	applycal::::	
 2019-08-07 13:00:58	INFO	applycal::::+	##########################################
 2019-08-07 13:00:58	INFO	applycal::::+	##### Begin Task: applycal #####
 2019-08-07 13:00:58	INFO	applycal::::	applycal(vis="XMMLSS12_1539286252_tiny.mms",field="0",spw="",intent="",selectdata=False,
 2019-08-07 13:00:58	INFO	applycal::::+ timerange="",uvrange="",antenna="",scan="",observation="",
 2019-08-07 13:00:58	INFO	applycal::::+ msselect="",docallib=False,callib="",gaintable=['/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.fluxscale', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.pcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.xdel', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.mms.xycal'],gainfield=['2', '0', '0', '2', '2', '2'],
 2019-08-07 13:00:58	INFO	applycal::::+ interp=[],spwmap=[],calwt=False,parang=True,applymode="",
 2019-08-07 13:00:58	INFO	applycal::::+ flagbackup=True)
 2019-08-07 13:00:58	INFO	applycal::AgentFlagger::open	Table type is Measurement Set
 2019-08-07 13:00:58	INFO	FlagVersion::saveFlagVersion	Creating new backup flag file called applycal_4
 2019-08-07 13:01:07	INFO	applycal::::	
 2019-08-07 13:01:07	INFO	applycal::::+	##########################################
 2019-08-07 13:01:07	INFO	applycal::::+	##### Begin Task: applycal #####
 2019-08-07 13:01:07	INFO	applycal::::	applycal(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",field="0",spw="",intent="",selectdata=False,
 2019-08-07 13:01:07	INFO	applycal::::+ timerange="",uvrange="",antenna="",scan="",observation="",
 2019-08-07 13:01:07	INFO	applycal::::+ msselect="",docallib=False,callib="",gaintable=['/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.kcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.fluxscale', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.pcal', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.xdel', '/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.mms.xycal'],gainfield=['2', '0', '0', '2', '2', '2'],
 2019-08-07 13:01:07	INFO	applycal::::+ interp=[],spwmap=[],calwt=[False],parang=True,applymode="",
 2019-08-07 13:01:07	INFO	applycal::::+ flagbackup=False)
 2019-08-07 13:01:07	INFO	applycal::calibrater::open	****Using NEW VI2-driven calibrater tool****
 2019-08-07 13:01:07	INFO	applycal::calibrater::open	Opening MS: /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms for calibration.
 2019-08-07 13:01:07	INFO	applycal::Calibrater::	Initializing nominal selection to the whole MS.
 2019-08-07 13:01:07	INFO	applycal::calibrater::setdata	Beginning selectvis--(MSSelection version)-------
 2019-08-07 13:01:07	INFO	applycal::calibrater::reset	Reseting solve/apply state
 2019-08-07 13:01:07	INFO	applycal::Calibrater::selectvis	Performing selection on MeasurementSet
 2019-08-07 13:01:07	INFO	applycal::Calibrater::selectvis+ Selecting on field: '0'
 2019-08-07 13:01:07	INFO	applycal::Calibrater::selectvis	Selection did not drop any rows
 2019-08-07 13:01:07	INFO	applycal::Calibrater::selectvis	Frequency selection: Selecting all channels in all spws.
 2019-08-07 13:01:07	INFO	applycal::calibrater::setdata	chanmode=none nchan=1 start=0 step=1 mStart='0km/s' mStep='0km/s' msSelect=''
 2019-08-07 13:01:07	INFO	applycal::calibrater::setapply	Beginning setapply--(MSSelection version)-------
 2019-08-07 13:01:07	INFO	applycal::Calibrater::setapply(type, applypar)	Arranging to APPLY:
 2019-08-07 13:01:07	INFO	applycal::Calibrater::setapply(type, applypar)	. K Jones: table=/scratch/mightee/MeerKAT-IRIS/caltables/

# Splitting out calibrated data 

Finally the calibrated data are averaged down in time and frequency by the amount specified in the config file, and the target(s) and calibrators are split out into separate MMSs for further imaging/processing.

In [15]:
run pipelines/processMeerKAT/cal_scripts/split.py --config myconfig.txt

Show log 2019-08-07 13:17:48	INFO	msmetadata_cmpt.cc::open	Performing internal consistency checks on XMMLSS12_1539286252_tiny.mms...
 2019-08-07 13:17:49	INFO	mstransform::::	
 2019-08-07 13:17:49	INFO	mstransform::::+	##########################################
 2019-08-07 13:17:49	INFO	mstransform::::+	##### Begin Task: mstransform #####
 2019-08-07 13:17:50	INFO	mstransform::::	mstransform(vis="XMMLSS12_1539286252_tiny.mms",outputvis="XMMLSS12_1539286252_tiny.J0217-0449.mms",createmms=True,separationaxis="auto",numsubms="auto",
 2019-08-07 13:17:50	INFO	mstransform::::+ tileshape=[0],field="J0217-0449",spw="0:860~1700MHz",scan="",antenna="",
 2019-08-07 13:17:50	INFO	mstransform::::+ correlation="",timerange="",intent="",array="",uvrange="",
 2019-08-07 13:17:50	INFO	mstransform::::+ observation="",feed="",datacolumn="corrected",realmodelcol=False,keepflags=False,
 2019-08-07 13:17:50	INFO	mstransform::::+ usewtspectrum=True,combinespws=False,chanaverage=False,chanbin=1,hanning=False,
 2019-08-07 13:17:50	INFO	mstransform::::+ regridms=False,mode="channel",nchan=-1,start=0,width=1,
 2019-08-07 13:17:50	INFO	mstransform::::+ nspw=1,interpolation="linear",phasecenter="",restfreq="",outframe="",
 2019-08-07 13:17:50	INFO	mstransform::::+ veltype="radio",preaverage=False,timeaverage=True,timebin="8s",timespan="",
 2019-08-07 13:17:50	INFO	mstransform::::+ maxuvwdistance=0.0,docallib=False,callib="",douvcontsub=False,fitspw="",
 2019-08-07 13:17:50	INFO	mstransform::::+ fitorder=0,want_cont=False,denoising_lib=True,nthreads=1,niter=1,
 2019-08-07 13:17:50	INFO	mstransform::::+ disableparallel=False,ddistart=-1,taql="",monolithic_processing=False,reindex=True)
 2019-08-07 13:17:50	INFO	ParallelDataHelper::::	Analyzing MS for partitioning
 2019-08-07 13:17:50	INFO	ParallelDataHelper::::	Input vis is a Multi-MS
 2019-08-07 13:17:50	INFO	mstransform::::	
 2019-08-07 13:17:50	INFO	mstransform::::+	##########################################
 2019-08-07 13:17:50	INFO	mstransform::::+	##### Begin Task: mstransform #####
 2019-08-07 13:17:50	INFO	mstransform::::	mstransform(vis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms",outputvis="/scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.J0217-0449.mms.data/XMMLSS12_1539286252_tiny.J0217-0449.mms.0000.ms",createmms=False,separationaxis="auto",numsubms="auto",
 2019-08-07 13:17:50	INFO	mstransform::::+ tileshape=[0],field="J0217-0449",spw="0:860~1700MHz",scan="",antenna="",
 2019-08-07 13:17:50	INFO	mstransform::::+ correlation="",timerange="",intent="",array="",uvrange="",
 2019-08-07 13:17:50	INFO	mstransform::::+ observation="",feed="",datacolumn="corrected",realmodelcol=False,keepflags=False,
 2019-08-07 13:17:50	INFO	mstransform::::+ usewtspectrum=True,combinespws=False,chanaverage=False,chanbin=1,hanning=False,
 2019-08-07 13:17:50	INFO	mstransform::::+ regridms=False,mode="channel",nchan=-1,start=0,width=1,
 2019-08-07 13:17:50	INFO	mstransform::::+ nspw=1,interpolation="linear",phasecenter="",restfreq="",outframe="",
 2019-08-07 13:17:50	INFO	mstransform::::+ veltype="radio",preaverage=False,timeaverage=True,timebin="8s",timespan="",
 2019-08-07 13:17:50	INFO	mstransform::::+ maxuvwdistance=0.0,docallib=False,callib="",douvcontsub=False,fitspw="",
 2019-08-07 13:17:50	INFO	mstransform::::+ fitorder=0,want_cont=False,denoising_lib=True,nthreads=1,niter=1,
 2019-08-07 13:17:50	INFO	mstransform::::+ disableparallel=False,ddistart=-1,taql="",monolithic_processing=False,reindex=True)
 2019-08-07 13:17:50	INFO	mstransform::::	Parse time averaging parameters
 2019-08-07 13:17:50	INFO	MSTransformManager::parseMsSpecParams	Input file name is /scratch/mightee/MeerKAT-IRIS/XMMLSS12_1539286252_tiny.mms/SUBMSS/XMMLSS12_1539286252_tiny.mms.0000.ms
 2019-08-07 13:17:50	INFO	MSTransformManager::parseMsSpecParams	Data column is CORRECTED
 2019-08-07 13:17:50	INFO	MSTransformManager::parseMsSpecParams	Output file name is /scratch/mightee/Mee

In [16]:
run pipelines/processMeerKAT/cal_scripts/quick_tclean.py --config myconfig.txt

Hide log 2019-08-07 13:28:31	INFO	msmetadata_cmpt.cc::open	Performing internal consistency checks on XMMLSS12_1539286252_tiny.mms...
 2019-08-07 13:28:31	INFO	tclean::::	
 2019-08-07 13:28:31	INFO	tclean::::+	##########################################
 2019-08-07 13:28:31	INFO	tclean::::+	##### Begin Task: tclean #####
 2019-08-07 13:28:31	INFO	tclean::::	tclean(vis="XMMLSS12_1539286252_tiny.J0217-0449.mms",selectdata=True,field="",spw="",timerange="",
 2019-08-07 13:28:31	INFO	tclean::::+ uvrange="",antenna="",scan="",observation="",intent="",
 2019-08-07 13:28:31	INFO	tclean::::+ datacolumn="corrected",imagename="/scratch/mightee/MeerKAT-IRIS/images/XMMLSS12_1539286252_tiny_J0217-0449.im",imsize=[2048, 2048],cell="2arcsec",phasecenter="",
 2019-08-07 13:28:31	INFO	tclean::::+ stokes="I",projection="SIN",startmodel="",specmode="mfs",reffreq="",
 2019-08-07 13:28:31	INFO	tclean::::+ nchan=-1,start="",width="",outframe="LSRK",veltype="radio",
 2019-08-07 13:28:31	INFO	tclean::::+ restfreq=[],interpolation="linear",perchanweightdensity=False,gridder="standard",facets=1,
 2019-08-07 13:28:31	INFO	tclean::::+ psfphasecenter="",chanchunks=1,wprojplanes=1,vptable="",usepointing=False,
 2019-08-07 13:28:31	INFO	tclean::::+ mosweight=True,aterm=True,psterm=False,wbawp=True,conjbeams=False,
 2019-08-07 13:28:31	INFO	tclean::::+ cfcache="",computepastep=360.0,rotatepastep=360.0,pblimit=0,normtype="flatnoise",
 2019-08-07 13:28:31	INFO	tclean::::+ deconvolver="mtmfs",scales=[],nterms=2,smallscalebias=0.6,restoration=True,
 2019-08-07 13:28:31	INFO	tclean::::+ restoringbeam=[],pbcor=False,outlierfile="",weighting="briggs",robust=0,
 2019-08-07 13:28:31	INFO	tclean::::+ noise="1.0Jy",npixels=0,uvtaper=[],niter=1000,gain=0.1,
 2019-08-07 13:28:31	INFO	tclean::::+ threshold=0,nsigma=0.0,cycleniter=-1,cyclefactor=1.0,minpsffraction=0.05,
 2019-08-07 13:28:31	INFO	tclean::::+ maxpsffraction=0.8,interactive=False,usemask="user",mask="",pbmask=0.0,
 2019-08-07 13:28:31	INFO	tclean::::+ sidelobethreshold=3.0,noisethreshold=5.0,lownoisethreshold=1.5,negativethreshold=0.0,smoothfactor=1.0,
 2019-08-07 13:28:31	INFO	tclean::::+ minbeamfrac=0.3,cutthreshold=0.01,growiterations=75,dogrowprune=True,minpercentchange=-1.0,
 2019-08-07 13:28:31	INFO	tclean::::+ verbose=False,fastnoise=True,restart=True,savemodel="none",calcres=True,
 2019-08-07 13:28:31	INFO	tclean::::+ calcpsf=True,parallel=True)
 2019-08-07 13:28:31	INFO	tclean::::	Verifying Input Parameters
 2019-08-07 13:28:31	SEVERE	tclean::MPIInterface::__init__::	MPI is not enabled
 2019-08-07 13:28:31	SEVERE	tclean::::	An error occurred running task tclean.
 2019-08-07 13:28:31	INFO	exportfits::utils::verify	Verifying arguments....File existence checking failed for imagename /scratch/mightee/MeerKAT-IRIS/images/XMMLSS12_1539286252_tiny_J0217-0449.im.image.tt0
 2019-08-07 13:28:31	WARN	exportfits::utils::verify	Argument imagename failed to verify.
 2019-08-07 13:28:31	SEVERE	exportfits::::	An error occurred running task exportfits.
 2019-08-07 13:28:31	INFO	tclean::::	
 2019-08-07 13:28:31	INFO	tclean::::+	##########################################
 2019-08-07 13:28:31	INFO	tclean::::+	##### Begin Task: tclean #####
 2019-08-07 13:28:31	INFO	tclean::::	tclean(vis="XMMLSS12_1539286252_tiny.J0521+1638.mms",selectdata=True,field="",spw="",timerange="",
 2019-08-07 13:28:31	INFO	tclean::::+ uvrange="",antenna="",scan="",observation="",intent="",
 2019-08-07 13:28:31	INFO	tclean::::+ datacolumn="corrected",imagename="/scratch/mightee/MeerKAT-IRIS/images/XMMLSS12_1539286252_tiny_J0521+1638.im",imsize=[2048, 2048],cell="2arcsec",phasecenter="",
 2019-08-07 13:28:31	INFO	tclean::::+ stokes="I",projection="SIN",startmodel="",specmode="mfs",reffreq="",
 2019-08-07 13:28:31	INFO	tclean::::+ nchan=-1,start="",width="",outframe="LSRK",veltype="radio",
 2019-08-07 13:28:31	INFO	tclean::::+ restfreq=[],interpolation="linear",perchanweightdensity=False,gridder="standard",facets=1,
 2019-08-07 13:28:31	INFO	tclean:

In [17]:
run pipelines/processMeerKAT/cal_scripts/plot_solutions.py --config myconfig.txt

/usr/local/lib/python2.7/dist-packages/matplotlib/cbook/deprecation.py:107: MatplotlibDeprecationWarning: Adding an axes using the same arguments as a previous axes currently reuses the earlier instance.  In a future version, a new instance will always be created and returned.  Meanwhile, this warning can be suppressed, and the future behavior ensured, by passing a unique label to each axes instance.
  warnings.warn(message, mplDeprecation, stacklevel=1)


Combining all plots into multi-page PDF "plots/bpass_freq_amp_all.pdf"
Combining all plots into multi-page PDF "plots/bpass_freq_phase_all.pdf"
Combining all plots into multi-page PDF "plots/phasecal_time_amp_all.pdf"
Combining all plots into multi-page PDF "plots/phasecal_time_phase_all.pdf"


Show log 2019-08-07 13:28:31	INFO	msmetadata_cmpt.cc::open	Performing internal consistency checks on XMMLSS12_1539286252_tiny.mms...
 2019-08-07 13:28:32	INFO	plotms::::	
 2019-08-07 13:28:32	INFO	plotms::::+	##########################################
 2019-08-07 13:28:32	INFO	plotms::::+	##### Begin Task: plotms #####
 2019-08-07 13:28:32	INFO	plotms::::	plotms(vis="/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal",gridrows=1,gridcols=1,rowindex=0,colindex=0,
 2019-08-07 13:28:32	INFO	plotms::::+ plotindex=0,xaxis="Real",xdatacolumn="",xframe="",xinterp="",
 2019-08-07 13:28:32	INFO	plotms::::+ yaxis="Imag",ydatacolumn="",yframe="",yinterp="",yaxislocation="",
 2019-08-07 13:28:32	INFO	plotms::::+ selectdata=True,field="",spw="",timerange="",uvrange="",
 2019-08-07 13:28:32	INFO	plotms::::+ antenna="",scan="",correlation="",array="",observation="",
 2019-08-07 13:28:32	INFO	plotms::::+ intent="",feed="",msselect="",averagedata=True,avgchannel="",
 2019-08-07 13:28:32	INFO	plotms::::+ avgtime="",avgscan=False,avgfield=False,avgbaseline=False,avgantenna=False,
 2019-08-07 13:28:32	INFO	plotms::::+ avgspw=False,scalar=False,transform=True,freqframe="",restfreq="",
 2019-08-07 13:28:32	INFO	plotms::::+ veldef="RADIO",shift=[0.0, 0.0],extendflag=False,extcorr=False,extchannel=False,
 2019-08-07 13:28:32	INFO	plotms::::+ iteraxis="",xselfscale=False,yselfscale=False,xsharedaxis=False,ysharedaxis=False,
 2019-08-07 13:28:32	INFO	plotms::::+ customsymbol=False,symbolshape="autoscaling",symbolsize=2,symbolcolor="0000ff",symbolfill="fill",
 2019-08-07 13:28:32	INFO	plotms::::+ symboloutline=False,coloraxis="corr",customflaggedsymbol=False,flaggedsymbolshape="circle",flaggedsymbolsize=2,
 2019-08-07 13:28:32	INFO	plotms::::+ flaggedsymbolcolor="ff0000",flaggedsymbolfill="fill",flaggedsymboloutline=False,xconnector="",timeconnector=False,
 2019-08-07 13:28:32	INFO	plotms::::+ plotrange=[],title="",titlefont=0,xlabel="",xaxisfont=0,
 2019-08-07 13:28:32	INFO	plotms::::+ ylabel="",yaxisfont=0,showmajorgrid=False,majorwidth=1,majorstyle="",
 2019-08-07 13:28:32	INFO	plotms::::+ majorcolor="B0B0B0",showminorgrid=False,minorwidth=1,minorstyle="",minorcolor="D0D0D0",
 2019-08-07 13:28:32	INFO	plotms::::+ showlegend=False,legendposition="",plotfile="plots/bpass_real_imag.png",expformat="",verbose=True,
 2019-08-07 13:28:32	INFO	plotms::::+ exprange="",highres=False,dpi=-1,width=-1,height=-1,
 2019-08-07 13:28:32	INFO	plotms::::+ overwrite=False,showgui=False,clearplots=True,callib=[''],headeritems="",
 2019-08-07 13:28:32	INFO	plotms::::+ showatm=False,showtsky=False)
 2019-08-07 13:28:32	SEVERE	plotms::::	ERROR: DISPLAY environment variable is not set! Cannot run plotms.
 2019-08-07 13:28:32	INFO	plotms::::	##### End Task: plotms #####
 2019-08-07 13:28:32	INFO	plotms::::+	##########################################
 2019-08-07 13:28:32	INFO	plotms::::	
 2019-08-07 13:28:32	INFO	plotms::::+	##########################################
 2019-08-07 13:28:32	INFO	plotms::::+	##### Begin Task: plotms #####
 2019-08-07 13:28:32	INFO	plotms::::	plotms(vis="/scratch/mightee/MeerKAT-IRIS/caltables/XMMLSS12_1539286252_tiny.bcal",gridrows=1,gridcols=1,rowindex=0,colindex=0,
 2019-08-07 13:28:32	INFO	plotms::::+ plotindex=0,xaxis="freq",xdatacolumn="",xframe="",xinterp="",
 2019-08-07 13:28:32	INFO	plotms::::+ yaxis="Amp",ydatacolumn="",yframe="",yinterp="",yaxislocation="",
 2019-08-07 13:28:32	INFO	plotms::::+ selectdata=True,field="",spw="",timerange="",uvrange="",
 2019-08-07 13:28:32	INFO	plotms::::+ antenna="",scan="",correlation="",array="",observation="",
 2019-08-07 13:28:32	INFO	plotms::::+ intent="",feed="",msselect="",averagedata=True,avgchannel="",
 2019-08-07 13:28:32	INFO	plotms::::+ avgtime="",avgscan=False,avgfield=False,avgbaseline=False,avgantenna=False,
 2019-08-07 13:28:32	INFO	plotms::::+ avgspw=False,scalar=False,transform=True,freqframe="",restfreq="",
 2019-08-07 13:28:32	INFO	plotms::::+ veldef="RADIO",shift=[0